# Google Colaboratoryb(略称: Colab)の環境設定

In [ ]:
%tensorflow_version 1.x
%load_ext tensorboard
!pip install stable-baselines[mpi]==2.10.0
!pip install gym-retro
!pip install git+https://github.com/openai/baselines > ~/pip_install_baselines.log

The tensorboard extension is already loaded. To reload it, use:
  %reload_ext tensorboard
  Running command git clone -q https://github.com/openai/baselines /tmp/pip-req-build-qxxw9m99


# ソニックのROMをColabにアップロード
　ソニックを強化学習環境として利用するためにOpenAIから提供されている[Gym Retro](https://github.com/openai/retro)ライブラリを利用します。

ここではソニックをColabで利用するために、以下の方法をとります。どちらかを選んでください。


### Steamから直接ダウンロード
　Gym Retroでは購入したゲームを直接ダウンロードするPythonスクリプトが用意されています。直接ダウンロードする場合は3つの情報が必要になります。  
　3つ目のSteamガードコードは、メールやSteamのスマホアプリで届くワンタイムトークンの入力が必要になります。(自分はメールが届かなかったので、アプリをインストールしました。)   
　何回かエラーが出ますが、放置してたらダウンロードが成功します。
```
Steam Username: "Steamのユーザー名"
Steam Password (leave blank if cached): "Steamのパスワード"
Steam Guard code:"Steamガードコード"
```

### GoogleドライブからROMをインポート
  SonicのROMファイル「SONIC_W.68K」を入手している場合はGoogleドライブからColabにアップロードしてGym Retroに強化学習環境をインポートします。手順は以下になります。
  1. SONIC_W.68KをローカルからGoogleドライブの任意の場所にアップロード
  2. アップロードした場所を指定
  


In [ ]:
#@title ## ROMのダウンロード方法を選択してください。
#@markdown ダウンロードを選択してください。
selected_download = 'Google\u30C9\u30E9\u30A4\u30D6\u304B\u3089ROM\u3092\u30A4\u30F3\u30DD\u30FC\u30C8' #@param ["Steamから直接ダウンロード", "GoogleドライブからROMをインポート"]

if selected_download == 'Steamから直接ダウンロード':
  !python -m retro.import.sega_classics
  
else:
  # Google Driveのマウント
  from google.colab import drive
  import os
  drive.mount('/content/drive')
  #@markdown GoogleドライブからROMをインポートする場合は、ROMのパスを入力してください:
  file_path = "Colab\\ Notebooks/OpenAI" #@param {type:"string"}
  
  !python -m retro.import /content/drive/MyDrive/{file_path}/

  #以下は使わな開
  #!cp /content/drive/MyDrive/{file_path}/SONIC_W.68K .
  #!mv SONIC_W.68K rom.md
  #!cp rom.md /usr/local/lib/python3.6/dist-packages/retro/data/stable/SonicTheHedgehog-Genesis/
  
  #@markdown セルを実行して以下にrom.mdが表示されていたら成功です。
  file_list = os.listdir('/usr/local/lib/python3.6/dist-packages/retro/data/stable/SonicTheHedgehog-Genesis/')
  print("強化学習環境一覧："+str(file_list))


Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).
Importing SonicTheHedgehog-Genesis
Imported 1 games
強化学習環境一覧：['ScrapBrainZone.Act2.state', 'GreenHillZone.Act2.state', 'rom.md', 'LabyrinthZone.Act1.state', 'MarbleZone.Act3.state', 'xpos.json', 'GreenHillZone.Act1.state', 'LabyrinthZone.Act2.state', 'MarbleZone.Act2.state', 'rom.sha', 'SpringYardZone.Act2.state', 'GreenHillZone.Act3.state', 'SpringYardZone.Act3.state', 'contest.json', 'script.lua', 'scenario.json', 'StarLightZone.Act2.state', 'LabyrinthZone.Act3.state', 'data.json', 'SpringYardZone.Act1.state', 'ScrapBrainZone.Act1.state', 'StarLightZone.Act3.state', 'metadata.json', 'StarLightZone.Act1.state', 'MarbleZone.Act1.state']


# モデルの学習
　学習を行う前に、コールバックとCustomRewardAndDoneラッパーを定義します。

## コールバック
　学習途中で行いたい処理を定義します。下記ではエピソードが学習更新が100ごとに、以下のログを表示しています。
*   出力時間
*   学習更新の総回数
*   100エピソードの中で最高報酬
*   100エピソードの中で最低報酬
*   累積報酬の平均
*   過去の累積報酬の最高報酬
*   モデルを保存したか(bool)

累積報酬の平均が過去の累積報酬の最高報酬を上回った場合に、モデルを保存します。


## CustomRewardAndDoneラッパー
報酬の与え方と終了条件を変更するクラスになります。
### 報酬の与え方
　報酬は2種類を定義します。
1. 「現在のX座標 - 過去にX座標の最大値」：負の値になるならば、0を与えます。
1. 「1フレーム前のX座標 - 現在のY座標」(仮)

### 終了条件
　終了条件は2種類を定義します。
1. 1回死んだら終了
1. 1面クリア(X座標が9600以上)

In [ ]:
import gym
import os
import numpy as np
import datetime
from stable_baselines.results_plotter import load_results, ts2xy

log_dir = './logs/'
os.makedirs(log_dir, exist_ok=True)

best_mean_reward = -np.inf
nupdates = 1
period_check = 100 

def callback(_locals, _globals):
    global nupdates
    global best_mean_reward
    nupdates += 1
    
    if nupdates % period_check == 0:

        x, y = ts2xy(load_results(log_dir), 'timesteps')
        if len(y) > 0:

            mean_reward = np.mean(y[-period_check:])
            max_reward = max(y[-period_check:])
            min_reward = min(y[-period_check:])

            update_model = mean_reward > best_mean_reward
            if update_model:
                best_mean_reward = mean_reward
                _locals['self'].save('model')

            print('time: {}, nupdates: {}, max_reward: {:.2f}, min_reward: {:.2f}, mean: {:.2f}, best_mean: {:.2f}, model_update: {}'.format(
                    datetime.datetime.now(),
                    nupdates-1, max_reward, min_reward,  mean_reward, best_mean_reward, update_model))

    return True


class CustomRewardAndDoneEnv(gym.Wrapper):

    def __init__(self, env):
        super(CustomRewardAndDoneEnv, self).__init__(env)
        self._cur_x = 0
        self._max_x = 0
        self._before_x = 0
        self._count_flame = 0
        
    def reset(self, **kwargs):
        self._cur_x = 0
        self._max_x = 0
        self._before_x =0
        self._count_flame = 0
        return self.env.reset(**kwargs)

    def step(self, action):
        state, reward, done, info = self.env.step(action)

        self._cur_x = info['x']
        reward = max(0, self._cur_x - self._max_x)
        self._max_x = max(self._max_x, self._cur_x)
        
        # if self._before_x == self._cur_x:
        #   self._count_flame += 1
        #   reward -= self._count_flame * 0.01

        # else :
        #   self._count_flame = 0

        self._before_x = self._cur_x

        if info['lives'] == 2 or info['x'] > 9600:
            done = True

        return state, reward, done, info

# 学習のための前処理
　エージェントが学習を効率的に行うために、学習しやすい強化学習環境に変換を行います。  
　前処理の詳細を以下に記載します。
*  SonicDiscretize  
　エージェントが取りえる行動を変化させます。今回の場合は、2^12から7通りに行動を変化します。
*  RewardScaler  
　報酬をscale倍にスケーリングします。
*  CustomRewardAndDoneEnv  
　報酬の与え方と終了条件を変更します。
*  StochasticFrameSkip  
　nフレームごとに行動を決定し、nフレームの間で連続的に同じ行動を取るようにします。
*  Downsample  
　画像サイズを小さくします。
* Rgb2gra  
　グレースケールします。
*  FrameStack  
　直近 k フレームをまとめて 1 つの状態としてエージェントに与えます。
*  ScaledFloatFrame  
　画素値を 255 で割って 0～1 に正規化します。
*  TimeLimit  
　一定時間経過するとエピソードを終了します。学習過程で壁にぶつかり続ける現象が確認できたため、その場合は失敗とみなします。
*  Monitor  
　monitor.csvにログを書き出します。


In [ ]:
import retro
import os
import time
from stable_baselines import PPO2
from stable_baselines.common.policies import CnnPolicy
from stable_baselines.common.vec_env import DummyVecEnv
from baselines.common.retro_wrappers import *
from stable_baselines.bench import Monitor
from stable_baselines.common import set_global_seeds

env = retro.make(game='SonicTheHedgehog-Genesis', state='GreenHillZone.Act1')
env = SonicDiscretizer(env)
env = RewardScaler(env, scale=0.01)
env = CustomRewardAndDoneEnv(env)
env = StochasticFrameSkip(env, n=4, stickprob=0.25)
env = Downsample(env, 2)
env = Rgb2gray(env)
env = FrameStack(env, 4)
env = ScaledFloatFrame(env)
env = TimeLimit(env, max_episode_steps=4500)
env = Monitor(env, log_dir, allow_early_resets=True)
print('行動空間: ', env.action_space)
print('状態空間: ', env.observation_space)

行動空間:  Discrete(7)
状態空間:  Box(112, 160, 4)


/usr/local/lib/python3.6/dist-packages/gym/logger.py:30: UserWarning: WARN: Box bound precision lowered by casting to float32
  warnings.warn(colorize('%s: %s'%('WARN', msg % args), 'yellow'))


# 学習





## シード値
　重みの初期化はランダムで行われます。学習を実行するたびに、重みはランダムに変化し、学習結果が異なるため再現性がない結果となります。そのため、シード値を固定することで再現性がある結果を出力するようにします。


## モデルの設定
　今回は強化学習アルゴリズムの一種であるPPO2を利用します。
方策の取り方してCNNPolicyを利用します。
PPO2の詳細は[モリカトロンさんの開発者ブログ](https://tech.morikatron.ai/entry/2020/06/29/100000)がとても参考になりました。

In [ ]:

env.seed(1234)
set_global_seeds(1234)

env = DummyVecEnv([lambda: env])

# モデルの生成
model = PPO2(policy=CnnPolicy, env=env, verbose=0, learning_rate=2.5e-5, tensorboard_log=log_dir)

# モデルの学習
model.learn(total_timesteps=200000, callback=callback)

env.close()

time: 2020-12-21 21:46:20.656262, nupdates: 24399, max_reward: 1852.00, min_reward: 1852.00, mean: 1852.00, best_mean: 1852.00, model_update: True
time: 2020-12-21 21:46:21.547650, nupdates: 24499, max_reward: 1852.00, min_reward: 1852.00, mean: 1852.00, best_mean: 1852.00, model_update: False
time: 2020-12-21 21:46:22.396632, nupdates: 24599, max_reward: 1852.00, min_reward: 1852.00, mean: 1852.00, best_mean: 1852.00, model_update: False
time: 2020-12-21 21:46:23.014559, nupdates: 24699, max_reward: 1852.00, min_reward: 1852.00, mean: 1852.00, best_mean: 1852.00, model_update: False
time: 2020-12-21 21:46:23.842361, nupdates: 24799, max_reward: 1852.00, min_reward: 1852.00, mean: 1852.00, best_mean: 1852.00, model_update: False
time: 2020-12-21 21:46:24.684484, nupdates: 24899, max_reward: 1852.00, min_reward: 1852.00, mean: 1852.00, best_mean: 1852.00, model_update: False
time: 2020-12-21 21:46:25.498616, nupdates: 24999, max_reward: 1852.00, min_reward: 1852.00, mean: 1852.00, best_

# 学習の過程を確認

In [ ]:
%tensorboard --logdir ./logs/

# 学習したモデルをローカルにダウンロード

In [ ]:
!mkdir model_result
!mv model.zip model_result/
!mv logs model_result/
!zip -r download_model.zip model_result

from google.colab import files
files.download("download_model.zip")

In [ ]:
ローカルで1.16.4

  adding: model_result/ (stored 0%)
  adding: model_result/logs/ (stored 0%)
  adding: model_result/logs/monitor.csv (deflated 26%)
  adding: model_result/sonic_model.zip (stored 0%)


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

# ローカルで実行するときには

In [ ]:

# モデルの読み込み
model = PPO2.load('model', env=env, verbose=0)

# モデルのテスト
state = env.reset()
total_reward = 0
env.close()



while True:
    # 環境の描画
    #env.render()

    # スリープ
    time.sleep(1/120)

    # モデルの推論
    action, _ = model.predict(state)

    # 1ステップ実行
    state, reward, done, info = env.step(action)
    total_reward += reward[0]

    # エピソード完了
    if done:
        print('reward:', total_reward)
        state = env.reset()
        total_reward = 0